In [1]:
import pandas as pd
import requests

In [2]:
baby_names = {}
for year in range(2015,2019):    
    response = requests.get(f"http://faculty.cs.niu.edu/~dakoop/cs680-2020sp/notebooks/baby-names-{year}.tsv", stream=True)

    # Tab-delimited file, need different separator
    df = pd.read_csv(response.raw, sep='\t')
    # Set a year column to disambiguate it from other years
    df["Year"] = year
    baby_names[year] = df

In [3]:
baby_names[2018]

Rank Male name Female name  Year
0     1      Liam        Emma  2018
1     2      Noah      Olivia  2018
2     3   William         Ava  2018
3     4     James    Isabella  2018
4     5    Oliver      Sophia  2018
5     6  Benjamin   Charlotte  2018
6     7    Elijah         Mia  2018
7     8     Lucas      Amelia  2018
8     9     Mason      Harper  2018
9    10     Logan      Evelyn  2018

In [4]:
# Concatenate data frames (one on top of the other)
df = pd.concat(baby_names.values())
df

Rank  Male name Female name  Year
0     1       Noah        Emma  2015
1     2       Liam      Olivia  2015
2     3      Mason      Sophia  2015
3     4      Jacob         Ava  2015
4     5    William    Isabella  2015
5     6      Ethan         Mia  2015
6     7      James     Abigail  2015
7     8  Alexander       Emily  2015
8     9    Michael   Charlotte  2015
9    10   Benjamin      Harper  2015
0     1       Noah        Emma  2016
1     2       Liam      Olivia  2016
2     3    William         Ava  2016
3     4      Mason      Sophia  2016
4     5      James    Isabella  2016
5     6   Benjamin         Mia  2016
6     7      Jacob   Charlotte  2016
7     8    Michael     Abigail  2016
8     9     Elijah       Emily  2016
9    10      Ethan      Harper  2016
0     1       Liam        Emma  2017
1     2       Noah      Olivia  2017
2     3    William         Ava  2017
3     4      James    Isabella  2017
4     5      Logan      Sophia  2017
5     6   Benjamin         Mia  2017
6     7      Mason   Charlotte  2017
7     8     Elijah      Amelia  2017
8     9     Oliver      Evelyn  2017
9    10      Jacob     Abigail  2017
0     1       Liam        Emma  2018
1     2       Noah      Olivia  2018
2     3    William         Ava  2018
3     4      James    Isabella  2018
4     5     Oliver      Sophia  2018
5     6   Benjamin   Charlotte  2018
6     7     Elijah         Mia  2018
7     8      Lucas      Amelia  2018
8     9      Mason      Harper  2018
9    10      Logan      Evelyn  2018

In [5]:
# search for particular ranks
df[df.Rank == 3]

Rank Male name Female name  Year
2     3     Mason      Sophia  2015
2     3   William         Ava  2016
2     3   William         Ava  2017
2     3   William         Ava  2018

In [6]:
# Tidy the data so that male names and female names are separate
df = df.melt(id_vars=["Rank","Year"])
df

Rank  Year     variable      value
0      1  2015    Male name       Noah
1      2  2015    Male name       Liam
2      3  2015    Male name      Mason
3      4  2015    Male name      Jacob
4      5  2015    Male name    William
..   ...   ...          ...        ...
75     6  2018  Female name  Charlotte
76     7  2018  Female name        Mia
77     8  2018  Female name     Amelia
78     9  2018  Female name     Harper
79    10  2018  Female name     Evelyn

[80 rows x 4 columns]

In [7]:
# rename the columns
df = df.rename(columns={"variable": "Gender","value": "Name"})

Rank  Year       Gender       Name
0      1  2015    Male name       Noah
1      2  2015    Male name       Liam
2      3  2015    Male name      Mason
3      4  2015    Male name      Jacob
4      5  2015    Male name    William
..   ...   ...          ...        ...
75     6  2018  Female name  Charlotte
76     7  2018  Female name        Mia
77     8  2018  Female name     Amelia
78     9  2018  Female name     Harper
79    10  2018  Female name     Evelyn

[80 rows x 4 columns]

In [8]:
# get rid fo the "name" part of the string
df["Gender"] = df["Gender"].str.split(' ').str[0]
df

Rank  Year  Gender       Name
0      1  2015    Male       Noah
1      2  2015    Male       Liam
2      3  2015    Male      Mason
3      4  2015    Male      Jacob
4      5  2015    Male    William
..   ...   ...     ...        ...
75     6  2018  Female  Charlotte
76     7  2018  Female        Mia
77     8  2018  Female     Amelia
78     9  2018  Female     Harper
79    10  2018  Female     Evelyn

[80 rows x 4 columns]

In [9]:
# Easier to search now
df[(df.Rank == 9) & (df.Year == 2016)]

Rank  Year  Gender    Name
18     9  2016    Male  Elijah
58     9  2016  Female   Emily

In [10]:
# What if we want to look at trends in how a name changes rank from year to year?
df.loc[df.Gender == "Male",["Rank","Year","Name"]].pivot(index="Name", columns="Year")

Rank                  
Year       2015  2016  2017  2018
Name                             
Alexander   8.0   NaN   NaN   NaN
Benjamin   10.0   6.0   6.0   6.0
Elijah      NaN   9.0   8.0   7.0
Ethan       6.0  10.0   NaN   NaN
Jacob       4.0   7.0  10.0   NaN
James       7.0   5.0   4.0   4.0
Liam        2.0   2.0   1.0   1.0
Logan       NaN   NaN   5.0  10.0
Lucas       NaN   NaN   NaN   8.0
Mason       3.0   4.0   7.0   9.0
Michael     9.0   8.0   NaN   NaN
Noah        1.0   1.0   2.0   2.0
Oliver      NaN   NaN   9.0   5.0
William     5.0   3.0   3.0   3.0

In [12]:
df.loc[df.Gender == "Female",["Rank","Year","Name"]].set_index(["Name","Year"]).unstack()

Rank                  
Year       2015  2016  2017  2018
Name                             
Abigail     7.0   8.0  10.0   NaN
Amelia      NaN   NaN   8.0   8.0
Ava         4.0   3.0   3.0   3.0
Charlotte   9.0   7.0   7.0   6.0
Emily       8.0   9.0   NaN   NaN
Emma        1.0   1.0   1.0   1.0
Evelyn      NaN   NaN   9.0  10.0
Harper     10.0  10.0   NaN   9.0
Isabella    5.0   5.0   4.0   4.0
Mia         6.0   6.0   6.0   7.0
Olivia      2.0   2.0   2.0   2.0
Sophia      3.0   4.0   5.0   5.0

In [13]:
by_year = df.loc[df.Gender == "Female",["Rank","Year","Name"]].set_index(["Name","Year"]).unstack(0)

Rank                                                               \
Name Abigail Amelia  Ava Charlotte Emily Emma Evelyn Harper Isabella  Mia   
Year                                                                        
2015     7.0    NaN  4.0       9.0   8.0  1.0    NaN   10.0      5.0  6.0   
2016     8.0    NaN  3.0       7.0   9.0  1.0    NaN   10.0      5.0  6.0   
2017    10.0    8.0  3.0       7.0   NaN  1.0    9.0    NaN      4.0  6.0   
2018     NaN    8.0  3.0       6.0   NaN  1.0   10.0    9.0      4.0  7.0   

                    
Name Olivia Sophia  
Year                
2015    2.0    3.0  
2016    2.0    4.0  
2017    2.0    5.0  
2018    2.0    5.0

In [14]:
by_name = by_year.stack().unstack(0)

Rank                  
Year       2015  2016  2017  2018
Name                             
Abigail     7.0   8.0  10.0   NaN
Amelia      NaN   NaN   8.0   8.0
Ava         4.0   3.0   3.0   3.0
Charlotte   9.0   7.0   7.0   6.0
Emily       8.0   9.0   NaN   NaN
Emma        1.0   1.0   1.0   1.0
Evelyn      NaN   NaN   9.0  10.0
Harper     10.0  10.0   NaN   9.0
Isabella    5.0   5.0   4.0   4.0
Mia         6.0   6.0   6.0   7.0
Olivia      2.0   2.0   2.0   2.0
Sophia      3.0   4.0   5.0   5.0

In [15]:
# does not work
by_name[2015]

KeyError: 2015

In [16]:
by_name[('Rank',2015)]

Name
Abigail       7.0
Amelia        NaN
Ava           4.0
Charlotte     9.0
Emily         8.0
Emma          1.0
Evelyn        NaN
Harper       10.0
Isabella      5.0
Mia           6.0
Olivia        2.0
Sophia        3.0
Name: (Rank, 2015), dtype: float64

In [17]:
# Get rid of the extra level of the column multiindex
by_name.columns = by_name.columns.get_level_values(1)

In [18]:
by_name

Year       2015  2016  2017  2018
Name                             
Abigail     7.0   8.0  10.0   NaN
Amelia      NaN   NaN   8.0   8.0
Ava         4.0   3.0   3.0   3.0
Charlotte   9.0   7.0   7.0   6.0
Emily       8.0   9.0   NaN   NaN
Emma        1.0   1.0   1.0   1.0
Evelyn      NaN   NaN   9.0  10.0
Harper     10.0  10.0   NaN   9.0
Isabella    5.0   5.0   4.0   4.0
Mia         6.0   6.0   6.0   7.0
Olivia      2.0   2.0   2.0   2.0
Sophia      3.0   4.0   5.0   5.0

In [19]:
by_name[2015]

Name
Abigail       7.0
Amelia        NaN
Ava           4.0
Charlotte     9.0
Emily         8.0
Emma          1.0
Evelyn        NaN
Harper       10.0
Isabella      5.0
Mia           6.0
Olivia        2.0
Sophia        3.0
Name: 2015, dtype: float64

In [21]:
# get back to rankings in order
by_name.stack().reset_index().set_index(["Year",0]).sort_index()

Name
Year 0              
2015 1.0        Emma
     2.0      Olivia
     3.0      Sophia
     4.0         Ava
     5.0    Isabella
     6.0         Mia
     7.0     Abigail
     8.0       Emily
     9.0   Charlotte
     10.0     Harper
2016 1.0        Emma
     2.0      Olivia
     3.0         Ava
     4.0      Sophia
     5.0    Isabella
     6.0         Mia
     7.0   Charlotte
     8.0     Abigail
     9.0       Emily
     10.0     Harper
2017 1.0        Emma
     2.0      Olivia
     3.0         Ava
     4.0    Isabella
     5.0      Sophia
     6.0         Mia
     7.0   Charlotte
     8.0      Amelia
     9.0      Evelyn
     10.0    Abigail
2018 1.0        Emma
     2.0      Olivia
     3.0         Ava
     4.0    Isabella
     5.0      Sophia
     6.0   Charlotte
     7.0         Mia
     8.0      Amelia
     9.0      Harper
     10.0     Evelyn